# РАЗДЕЛ 3. Конструирование признаков

Произведем тонкую настройку модели полносвязной нейронной сети с помощью гиперпараметров(количество скрытых слоев и количество нейронов)

In [5]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error
from sklearn.preprocessing import MinMaxScaler, StandardScaler, LabelEncoder
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense
%matplotlib inline 
sns.set(style="ticks")

In [2]:
# Подготовка данных для обучения
path_1 = r'./Data/X.xlsx'
X = pd.read_excel(path_1,index_col=0)
X.head()

Соотношение матрица-наполнитель  Плотность, кг/м3  модуль упругости, ГПа  \
0                         1.857143            2030.0             738.736842   
1                         1.857143            2030.0             738.736842   
2                         1.857143            2030.0             738.736842   
3                         1.857143            2030.0             738.736842   
4                         2.771331            2030.0             753.000000   

   Количество отвердителя, м.%  Содержание эпоксидных групп,%_2  \
0                        30.00                        22.267857   
1                        50.00                        23.750000   
2                        49.90                        33.000000   
3                       129.00                        21.250000   
4                       111.86                        22.267857   

   Температура вспышки, С_2  Поверхностная плотность, г/м2  \
0                100.000000                          210.0   
1                284.615385                          210.0   
2                284.615385                          210.0   
3                300.000000                          210.0   
4                284.615385                          210.0   

   Потребление смолы, г/м2  Угол нашивки, град  Шаг нашивки  Плотность нашивки  
0                    220.0                   0          4.0               57.0  
1                    220.0                   0          4.0               60.0  
2                    220.0                   0          4.0               70.0  
3                    220.0                   0          5.0               47.0  
4                    220.0                   0          5.0               57.0

In [3]:
path_2 = r'./Data/y.xlsx'
y = pd.read_excel(path_2,index_col=0)
y1 = y.drop(columns='Прочность при растяжении, МПа')
y2 = y.drop(columns='Модуль упругости при растяжении, ГПа')
y2.head()

Прочность при растяжении, МПа
0                         3000.0
1                         3000.0
2                         3000.0
3                         3000.0
4                         3000.0

In [6]:
# кодирование признака "Угол нашивки, град"
le = LabelEncoder()
X_le = X.copy()

X_le['Угол нашивки, град'] = le.fit_transform(X_le['Угол нашивки, град'])
X_le.head()

Соотношение матрица-наполнитель  Плотность, кг/м3  модуль упругости, ГПа  \
0                         1.857143            2030.0             738.736842   
1                         1.857143            2030.0             738.736842   
2                         1.857143            2030.0             738.736842   
3                         1.857143            2030.0             738.736842   
4                         2.771331            2030.0             753.000000   

   Количество отвердителя, м.%  Содержание эпоксидных групп,%_2  \
0                        30.00                        22.267857   
1                        50.00                        23.750000   
2                        49.90                        33.000000   
3                       129.00                        21.250000   
4                       111.86                        22.267857   

   Температура вспышки, С_2  Поверхностная плотность, г/м2  \
0                100.000000                          210.0   
1                284.615385                          210.0   
2                284.615385                          210.0   
3                300.000000                          210.0   
4                284.615385                          210.0   

   Потребление смолы, г/м2  Угол нашивки, град  Шаг нашивки  Плотность нашивки  
0                    220.0                   0          4.0               57.0  
1                    220.0                   0          4.0               60.0  
2                    220.0                   0          4.0               70.0  
3                    220.0                   0          5.0               47.0  
4                    220.0                   0          5.0               57.0

In [7]:
# стандартизация  данных
scaler_std = StandardScaler()
scaler_std.fit(X_le)
Xstd = pd.DataFrame (data =scaler_std.transform(X_le), columns=X_le.columns)
scaler_std_y = StandardScaler()
scaler_std_y.fit(y)
ystd = pd.DataFrame (data = scaler_std_y.transform(y), columns=y.columns)

In [9]:
#разбиение  данных на тестовую и тренировочную часть
X_train_norm, X_test_norm, y_train_norm, y_test_norm = train_test_split(Xnorm,ynorm, test_size=0.2, random_state=42, shuffle=True)


In [25]:
# оптимизируем однослойную сеть
def ml_model1D(Number1D):
    modelNN_y1 = Sequential()
    modelNN_y1.add(Dense(Number1D,  input_dim=11, activation = 'sigmoid'))
    modelNN_y1.add(Dense(2, activation = 'linear'))
    modelNN_y1.compile(optimizer='adam', loss='mse', metrics=['mae'])
    return modelNN_y1


In [27]:
modelsMAE=[]
for Num in range(11,100):
    modelNN = ml_model1D(Num)
    history = modelNN.fit(X_train_std,y_train_std, 
                    epochs=100, 
                    validation_split=0.1, 
                    verbose=2)
    y_pred = modelNN.predict(X_test_std)
    y_pred = scaler_std_y.inverse_transform (y_pred)
    MAENN_1 = mean_absolute_error(y_test.iloc[:,0],y_pred[:,0])
    MAENN_2 = mean_absolute_error(y_test.iloc[:,1],y_pred[:,1])
    modelsMAE.append([Num,MAENN_1,MAENN_2])

Epoch 1/100
23/23 - 0s - loss: 1.6784 - mae: 1.0386 - val_loss: 1.6526 - val_mae: 0.9837 - 490ms/epoch - 21ms/step
Epoch 2/100
23/23 - 0s - loss: 1.4799 - mae: 0.9738 - val_loss: 1.4916 - val_mae: 0.9316 - 57ms/epoch - 2ms/step
Epoch 3/100
23/23 - 0s - loss: 1.3388 - mae: 0.9251 - val_loss: 1.3733 - val_mae: 0.8941 - 50ms/epoch - 2ms/step
Epoch 4/100
23/23 - 0s - loss: 1.2408 - mae: 0.8912 - val_loss: 1.2862 - val_mae: 0.8650 - 45ms/epoch - 2ms/step
Epoch 5/100
23/23 - 0s - loss: 1.1699 - mae: 0.8659 - val_loss: 1.2258 - val_mae: 0.8477 - 49ms/epoch - 2ms/step
Epoch 6/100
23/23 - 0s - loss: 1.1217 - mae: 0.8472 - val_loss: 1.1814 - val_mae: 0.8368 - 45ms/epoch - 2ms/step
Epoch 7/100
23/23 - 0s - loss: 1.0882 - mae: 0.8350 - val_loss: 1.1483 - val_mae: 0.8299 - 50ms/epoch - 2ms/step
Epoch 8/100
23/23 - 0s - loss: 1.0645 - mae: 0.8258 - val_loss: 1.1253 - val_mae: 0.8244 - 46ms/epoch - 2ms/step
Epoch 9/100
23/23 - 0s - loss: 1.0498 - mae: 0.8211 - val_loss: 1.1095 - val_mae: 0.8215 - 50m

Epoch 73/100
23/23 - 0s - loss: 0.9899 - mae: 0.7967 - val_loss: 1.0196 - val_mae: 0.7943 - 44ms/epoch - 2ms/step
Epoch 74/100
23/23 - 0s - loss: 0.9912 - mae: 0.7970 - val_loss: 1.0228 - val_mae: 0.7966 - 44ms/epoch - 2ms/step
Epoch 75/100
23/23 - 0s - loss: 0.9891 - mae: 0.7964 - val_loss: 1.0207 - val_mae: 0.7954 - 39ms/epoch - 2ms/step
Epoch 76/100
23/23 - 0s - loss: 0.9897 - mae: 0.7964 - val_loss: 1.0198 - val_mae: 0.7944 - 45ms/epoch - 2ms/step
Epoch 77/100
23/23 - 0s - loss: 0.9892 - mae: 0.7964 - val_loss: 1.0208 - val_mae: 0.7955 - 40ms/epoch - 2ms/step
Epoch 78/100
23/23 - 0s - loss: 0.9892 - mae: 0.7964 - val_loss: 1.0224 - val_mae: 0.7964 - 41ms/epoch - 2ms/step
Epoch 79/100
23/23 - 0s - loss: 0.9892 - mae: 0.7964 - val_loss: 1.0215 - val_mae: 0.7957 - 43ms/epoch - 2ms/step
Epoch 80/100
23/23 - 0s - loss: 0.9891 - mae: 0.7962 - val_loss: 1.0216 - val_mae: 0.7956 - 39ms/epoch - 2ms/step
Epoch 81/100
23/23 - 0s - loss: 0.9895 - mae: 0.7965 - val_loss: 1.0221 - val_mae: 0.795

Epoch 45/100
23/23 - 0s - loss: 0.9949 - mae: 0.7986 - val_loss: 1.0271 - val_mae: 0.7983 - 40ms/epoch - 2ms/step
Epoch 46/100
23/23 - 0s - loss: 0.9945 - mae: 0.7984 - val_loss: 1.0277 - val_mae: 0.7989 - 44ms/epoch - 2ms/step
Epoch 47/100
23/23 - 0s - loss: 0.9946 - mae: 0.7984 - val_loss: 1.0264 - val_mae: 0.7978 - 41ms/epoch - 2ms/step
Epoch 48/100
23/23 - 0s - loss: 0.9944 - mae: 0.7985 - val_loss: 1.0266 - val_mae: 0.7986 - 42ms/epoch - 2ms/step
Epoch 49/100
23/23 - 0s - loss: 0.9945 - mae: 0.7986 - val_loss: 1.0282 - val_mae: 0.7994 - 40ms/epoch - 2ms/step
Epoch 50/100
23/23 - 0s - loss: 0.9943 - mae: 0.7986 - val_loss: 1.0263 - val_mae: 0.7984 - 40ms/epoch - 2ms/step
Epoch 51/100
23/23 - 0s - loss: 0.9945 - mae: 0.7986 - val_loss: 1.0274 - val_mae: 0.7989 - 42ms/epoch - 2ms/step
Epoch 52/100
23/23 - 0s - loss: 0.9943 - mae: 0.7983 - val_loss: 1.0278 - val_mae: 0.7993 - 40ms/epoch - 2ms/step
Epoch 53/100
23/23 - 0s - loss: 0.9943 - mae: 0.7983 - val_loss: 1.0245 - val_mae: 0.797

Epoch 17/100
23/23 - 0s - loss: 1.0023 - mae: 0.8011 - val_loss: 1.0325 - val_mae: 0.8002 - 42ms/epoch - 2ms/step
Epoch 18/100
23/23 - 0s - loss: 1.0009 - mae: 0.8005 - val_loss: 1.0304 - val_mae: 0.7996 - 44ms/epoch - 2ms/step
Epoch 19/100
23/23 - 0s - loss: 1.0003 - mae: 0.8005 - val_loss: 1.0291 - val_mae: 0.7989 - 42ms/epoch - 2ms/step
Epoch 20/100
23/23 - 0s - loss: 0.9992 - mae: 0.8003 - val_loss: 1.0293 - val_mae: 0.7995 - 40ms/epoch - 2ms/step
Epoch 21/100
23/23 - 0s - loss: 0.9980 - mae: 0.7998 - val_loss: 1.0281 - val_mae: 0.7993 - 40ms/epoch - 2ms/step
Epoch 22/100
23/23 - 0s - loss: 0.9977 - mae: 0.7998 - val_loss: 1.0266 - val_mae: 0.7988 - 41ms/epoch - 2ms/step
Epoch 23/100
23/23 - 0s - loss: 0.9971 - mae: 0.7995 - val_loss: 1.0266 - val_mae: 0.7989 - 42ms/epoch - 2ms/step
Epoch 24/100
23/23 - 0s - loss: 0.9961 - mae: 0.7991 - val_loss: 1.0254 - val_mae: 0.7984 - 42ms/epoch - 2ms/step
Epoch 25/100
23/23 - 0s - loss: 0.9958 - mae: 0.7991 - val_loss: 1.0232 - val_mae: 0.797

Epoch 89/100
23/23 - 0s - loss: 0.9872 - mae: 0.7960 - val_loss: 1.0188 - val_mae: 0.7971 - 39ms/epoch - 2ms/step
Epoch 90/100
23/23 - 0s - loss: 0.9875 - mae: 0.7961 - val_loss: 1.0184 - val_mae: 0.7970 - 39ms/epoch - 2ms/step
Epoch 91/100
23/23 - 0s - loss: 0.9883 - mae: 0.7965 - val_loss: 1.0187 - val_mae: 0.7964 - 44ms/epoch - 2ms/step
Epoch 92/100
23/23 - 0s - loss: 0.9866 - mae: 0.7959 - val_loss: 1.0176 - val_mae: 0.7966 - 39ms/epoch - 2ms/step
Epoch 93/100
23/23 - 0s - loss: 0.9871 - mae: 0.7961 - val_loss: 1.0195 - val_mae: 0.7979 - 39ms/epoch - 2ms/step
Epoch 94/100
23/23 - 0s - loss: 0.9871 - mae: 0.7962 - val_loss: 1.0200 - val_mae: 0.7986 - 39ms/epoch - 2ms/step
Epoch 95/100
23/23 - 0s - loss: 0.9865 - mae: 0.7959 - val_loss: 1.0205 - val_mae: 0.7980 - 40ms/epoch - 2ms/step
Epoch 96/100
23/23 - 0s - loss: 0.9865 - mae: 0.7958 - val_loss: 1.0200 - val_mae: 0.7975 - 40ms/epoch - 2ms/step
Epoch 97/100
23/23 - 0s - loss: 0.9867 - mae: 0.7958 - val_loss: 1.0205 - val_mae: 0.798

...

Epoch 69/100
23/23 - 0s - loss: 0.9952 - mae: 0.7996 - val_loss: 1.0171 - val_mae: 0.7928 - 43ms/epoch - 2ms/step
Epoch 70/100
23/23 - 0s - loss: 1.0001 - mae: 0.8020 - val_loss: 1.0118 - val_mae: 0.7904 - 43ms/epoch - 2ms/step
Epoch 71/100
23/23 - 0s - loss: 1.0063 - mae: 0.8040 - val_loss: 1.0173 - val_mae: 0.7923 - 43ms/epoch - 2ms/step
Epoch 72/100
23/23 - 0s - loss: 0.9955 - mae: 0.7999 - val_loss: 1.0131 - val_mae: 0.7908 - 42ms/epoch - 2ms/step
Epoch 73/100
23/23 - 0s - loss: 0.9956 - mae: 0.7992 - val_loss: 1.0173 - val_mae: 0.7931 - 41ms/epoch - 2ms/step
Epoch 74/100
23/23 - 0s - loss: 0.9965 - mae: 0.7996 - val_loss: 1.0113 - val_mae: 0.7900 - 44ms/epoch - 2ms/step
Epoch 75/100
23/23 - 0s - loss: 0.9945 - mae: 0.7991 - val_loss: 1.0302 - val_mae: 0.8009 - 40ms/epoch - 2ms/step
Epoch 76/100
23/23 - 0s - loss: 0.9930 - mae: 0.7980 - val_loss: 1.0100 - val_mae: 0.7898 - 41ms/epoch - 2ms/step
Epoch 77/100
23/23 - 0s - loss: 0.9990 - mae: 0.8003 - val_loss: 1.0174 - val_mae: 0.790

Epoch 41/100
23/23 - 0s - loss: 0.9980 - mae: 0.8000 - val_loss: 1.0176 - val_mae: 0.7946 - 42ms/epoch - 2ms/step
Epoch 42/100
23/23 - 0s - loss: 1.0033 - mae: 0.8013 - val_loss: 1.0256 - val_mae: 0.8006 - 42ms/epoch - 2ms/step
Epoch 43/100
23/23 - 0s - loss: 0.9992 - mae: 0.8000 - val_loss: 1.0149 - val_mae: 0.7880 - 43ms/epoch - 2ms/step
Epoch 44/100
23/23 - 0s - loss: 0.9996 - mae: 0.8010 - val_loss: 1.0298 - val_mae: 0.8013 - 41ms/epoch - 2ms/step
Epoch 45/100
23/23 - 0s - loss: 0.9997 - mae: 0.8004 - val_loss: 1.0282 - val_mae: 0.7996 - 44ms/epoch - 2ms/step
Epoch 46/100
23/23 - 0s - loss: 0.9990 - mae: 0.8003 - val_loss: 1.0231 - val_mae: 0.7975 - 43ms/epoch - 2ms/step
Epoch 47/100
23/23 - 0s - loss: 0.9994 - mae: 0.7992 - val_loss: 1.0288 - val_mae: 0.8021 - 40ms/epoch - 2ms/step
Epoch 48/100
23/23 - 0s - loss: 0.9982 - mae: 0.8007 - val_loss: 1.0212 - val_mae: 0.7912 - 45ms/epoch - 2ms/step
Epoch 49/100
23/23 - 0s - loss: 0.9995 - mae: 0.8012 - val_loss: 1.0148 - val_mae: 0.792

Epoch 13/100
23/23 - 0s - loss: 1.0000 - mae: 0.8018 - val_loss: 1.0150 - val_mae: 0.7896 - 45ms/epoch - 2ms/step
Epoch 14/100
23/23 - 0s - loss: 1.0037 - mae: 0.8013 - val_loss: 1.0253 - val_mae: 0.8001 - 43ms/epoch - 2ms/step
Epoch 15/100
23/23 - 0s - loss: 1.0003 - mae: 0.8008 - val_loss: 1.0129 - val_mae: 0.7922 - 40ms/epoch - 2ms/step
Epoch 16/100
23/23 - 0s - loss: 0.9988 - mae: 0.8004 - val_loss: 1.0166 - val_mae: 0.7912 - 45ms/epoch - 2ms/step
Epoch 17/100
23/23 - 0s - loss: 0.9989 - mae: 0.8000 - val_loss: 1.0194 - val_mae: 0.7973 - 41ms/epoch - 2ms/step
Epoch 18/100
23/23 - 0s - loss: 1.0001 - mae: 0.8015 - val_loss: 1.0086 - val_mae: 0.7879 - 41ms/epoch - 2ms/step
Epoch 19/100
23/23 - 0s - loss: 0.9989 - mae: 0.8003 - val_loss: 1.0181 - val_mae: 0.7952 - 42ms/epoch - 2ms/step
Epoch 20/100
23/23 - 0s - loss: 0.9986 - mae: 0.8007 - val_loss: 1.0197 - val_mae: 0.7951 - 44ms/epoch - 2ms/step
Epoch 21/100
23/23 - 0s - loss: 1.0003 - mae: 0.8007 - val_loss: 1.0240 - val_mae: 0.800

Epoch 85/100
23/23 - 0s - loss: 0.9953 - mae: 0.7995 - val_loss: 1.0179 - val_mae: 0.7952 - 40ms/epoch - 2ms/step
Epoch 86/100
23/23 - 0s - loss: 0.9956 - mae: 0.7997 - val_loss: 1.0315 - val_mae: 0.7989 - 42ms/epoch - 2ms/step
Epoch 87/100
23/23 - 0s - loss: 0.9950 - mae: 0.7984 - val_loss: 1.0166 - val_mae: 0.7950 - 46ms/epoch - 2ms/step
Epoch 88/100
23/23 - 0s - loss: 0.9986 - mae: 0.8007 - val_loss: 1.0119 - val_mae: 0.7894 - 48ms/epoch - 2ms/step
Epoch 89/100
23/23 - 0s - loss: 1.0031 - mae: 0.8021 - val_loss: 1.0330 - val_mae: 0.8044 - 42ms/epoch - 2ms/step
Epoch 90/100
23/23 - 0s - loss: 0.9964 - mae: 0.7998 - val_loss: 1.0253 - val_mae: 0.7982 - 40ms/epoch - 2ms/step
Epoch 91/100
23/23 - 0s - loss: 0.9960 - mae: 0.7995 - val_loss: 1.0158 - val_mae: 0.7912 - 44ms/epoch - 2ms/step
Epoch 92/100
23/23 - 0s - loss: 1.0023 - mae: 0.8027 - val_loss: 1.0144 - val_mae: 0.7917 - 44ms/epoch - 2ms/step
Epoch 93/100
23/23 - 0s - loss: 0.9988 - mae: 0.8003 - val_loss: 1.0350 - val_mae: 0.802

Epoch 57/100
23/23 - 0s - loss: 0.9994 - mae: 0.8009 - val_loss: 1.0186 - val_mae: 0.7921 - 44ms/epoch - 2ms/step
Epoch 58/100
23/23 - 0s - loss: 1.0014 - mae: 0.8027 - val_loss: 1.0251 - val_mae: 0.7992 - 44ms/epoch - 2ms/step
Epoch 59/100
23/23 - 0s - loss: 1.0019 - mae: 0.8016 - val_loss: 1.0141 - val_mae: 0.7895 - 43ms/epoch - 2ms/step
Epoch 60/100
23/23 - 0s - loss: 0.9994 - mae: 0.8007 - val_loss: 1.0166 - val_mae: 0.7944 - 43ms/epoch - 2ms/step
Epoch 61/100
23/23 - 0s - loss: 1.0065 - mae: 0.8051 - val_loss: 1.0105 - val_mae: 0.7892 - 43ms/epoch - 2ms/step
Epoch 62/100
23/23 - 0s - loss: 0.9995 - mae: 0.8014 - val_loss: 1.0209 - val_mae: 0.7956 - 46ms/epoch - 2ms/step
Epoch 63/100
23/23 - 0s - loss: 0.9967 - mae: 0.7994 - val_loss: 1.0180 - val_mae: 0.7944 - 45ms/epoch - 2ms/step
Epoch 64/100
23/23 - 0s - loss: 0.9979 - mae: 0.8007 - val_loss: 1.0183 - val_mae: 0.7950 - 45ms/epoch - 2ms/step
Epoch 65/100
23/23 - 0s - loss: 0.9964 - mae: 0.8005 - val_loss: 1.0255 - val_mae: 0.796

In [28]:
modelsMAE


[[11, 2.460988142772665, 361.40824067405435],
 [12, 2.4561492101705547, 359.34371236228384],
 [13, 2.4571583728007713, 359.935470977101],
 [14, 2.455155636019799, 360.94629115868736],
 [15, 2.456451445843668, 358.98197627203166],
 [16, 2.460861102084523, 358.7470632495533],
 [17, 2.4561569631830915, 358.7746824554091],
 [18, 2.460649871812888, 359.98497208955547],
 [19, 2.4620555276554867, 358.97323912359906],
 [20, 2.4525028827527766, 360.73508046417436],
 [21, 2.4589237030456266, 360.3963810432748],
 [22, 2.451957633187048, 361.1998277488542],
 [23, 2.455049361420645, 360.25972199428105],
 [24, 2.4468106277643447, 358.4280839476824],
 [25, 2.444551837881104, 359.49409032027273],
 [26, 2.456978281873275, 360.8446673548702],
 [27, 2.4543132464840784, 360.47134392790696],
 [28, 2.4441343441009256, 359.0622612677764],
 [29, 2.4574407364067397, 359.3898146399934],
 [30, 2.4619623769655368, 358.8868846281171],
 [31, 2.448570711993911, 359.42367135594264],
 [32, 2.4536407427355234, 359.1443

In [29]:
# оптимизируем двуслойную сеть
def ml_model2D(Number1D, Number2D):
    modelNN_y1 = Sequential()
    modelNN_y1.add(Dense(Number1D,  input_dim=11, activation = 'sigmoid'))
    modelNN_y1.add(Dense(Number2D,   activation = 'sigmoid'))
    modelNN_y1.add(Dense(2, activation = 'linear'))
    modelNN_y1.compile(optimizer='adam', loss='mse', metrics=['mae'])
    return modelNN_y1

In [30]:
modelsMAE_2D=[]
for Num1 in range(11,100,4):
    for Num2 in range(11,100,4):
        print ('Количество элементов ', Num1, '  ', Num2)
        modelNN = ml_model2D(Num1,Num2)
        history = modelNN.fit(X_train_std,y_train_std, 
                    epochs=100, 
                    validation_split=0.1, 
                    verbose=2)
        y_pred = modelNN.predict(X_test_std)
        y_pred = scaler_std_y.inverse_transform (y_pred)
        MAENN_1 = mean_absolute_error(y_test.iloc[:,0],y_pred[:,0])
        MAENN_2 = mean_absolute_error(y_test.iloc[:,1],y_pred[:,1])
        modelsMAE.append([Num1,Num2,MAENN_1,MAENN_2])

Количество элементов  11    11
Epoch 1/100
23/23 - 0s - loss: 1.2404 - mae: 0.8926 - val_loss: 1.2529 - val_mae: 0.8873 - 487ms/epoch - 21ms/step
Epoch 2/100
23/23 - 0s - loss: 1.1146 - mae: 0.8449 - val_loss: 1.1367 - val_mae: 0.8432 - 53ms/epoch - 2ms/step
Epoch 3/100
23/23 - 0s - loss: 1.0535 - mae: 0.8213 - val_loss: 1.0768 - val_mae: 0.8170 - 47ms/epoch - 2ms/step
Epoch 4/100
23/23 - 0s - loss: 1.0253 - mae: 0.8096 - val_loss: 1.0512 - val_mae: 0.8043 - 45ms/epoch - 2ms/step
Epoch 5/100
23/23 - 0s - loss: 1.0156 - mae: 0.8050 - val_loss: 1.0394 - val_mae: 0.7966 - 42ms/epoch - 2ms/step
Epoch 6/100
23/23 - 0s - loss: 1.0126 - mae: 0.8038 - val_loss: 1.0327 - val_mae: 0.7929 - 45ms/epoch - 2ms/step
Epoch 7/100
23/23 - 0s - loss: 1.0117 - mae: 0.8034 - val_loss: 1.0300 - val_mae: 0.7911 - 58ms/epoch - 3ms/step
Epoch 8/100
23/23 - 0s - loss: 1.0109 - mae: 0.8029 - val_loss: 1.0301 - val_mae: 0.7911 - 40ms/epoch - 2ms/step
Epoch 9/100
23/23 - 0s - loss: 1.0106 - mae: 0.8028 - val_loss:

Epoch 73/100
23/23 - 0s - loss: 0.9938 - mae: 0.7982 - val_loss: 1.0249 - val_mae: 0.7951 - 45ms/epoch - 2ms/step
Epoch 74/100
23/23 - 0s - loss: 0.9934 - mae: 0.7981 - val_loss: 1.0253 - val_mae: 0.7953 - 45ms/epoch - 2ms/step
Epoch 75/100
23/23 - 0s - loss: 0.9927 - mae: 0.7976 - val_loss: 1.0269 - val_mae: 0.7964 - 42ms/epoch - 2ms/step
Epoch 76/100
23/23 - 0s - loss: 0.9942 - mae: 0.7984 - val_loss: 1.0258 - val_mae: 0.7958 - 44ms/epoch - 2ms/step
Epoch 77/100
23/23 - 0s - loss: 0.9924 - mae: 0.7976 - val_loss: 1.0241 - val_mae: 0.7952 - 44ms/epoch - 2ms/step
Epoch 78/100
23/23 - 0s - loss: 0.9926 - mae: 0.7976 - val_loss: 1.0256 - val_mae: 0.7958 - 41ms/epoch - 2ms/step
Epoch 79/100
23/23 - 0s - loss: 0.9942 - mae: 0.7985 - val_loss: 1.0241 - val_mae: 0.7951 - 44ms/epoch - 2ms/step
Epoch 80/100
23/23 - 0s - loss: 0.9920 - mae: 0.7975 - val_loss: 1.0266 - val_mae: 0.7965 - 44ms/epoch - 2ms/step
Epoch 81/100
23/23 - 0s - loss: 0.9923 - mae: 0.7976 - val_loss: 1.0289 - val_mae: 0.798

Epoch 45/100
23/23 - 0s - loss: 0.9972 - mae: 0.7993 - val_loss: 1.0136 - val_mae: 0.7905 - 41ms/epoch - 2ms/step
Epoch 46/100
23/23 - 0s - loss: 0.9976 - mae: 0.7993 - val_loss: 1.0194 - val_mae: 0.7942 - 44ms/epoch - 2ms/step
Epoch 47/100
23/23 - 0s - loss: 0.9969 - mae: 0.7991 - val_loss: 1.0154 - val_mae: 0.7920 - 40ms/epoch - 2ms/step
Epoch 48/100
23/23 - 0s - loss: 0.9964 - mae: 0.7990 - val_loss: 1.0148 - val_mae: 0.7914 - 39ms/epoch - 2ms/step
Epoch 49/100
23/23 - 0s - loss: 0.9957 - mae: 0.7989 - val_loss: 1.0153 - val_mae: 0.7920 - 39ms/epoch - 2ms/step
Epoch 50/100
23/23 - 0s - loss: 0.9960 - mae: 0.7990 - val_loss: 1.0146 - val_mae: 0.7917 - 40ms/epoch - 2ms/step
Epoch 51/100
23/23 - 0s - loss: 0.9945 - mae: 0.7986 - val_loss: 1.0167 - val_mae: 0.7928 - 40ms/epoch - 2ms/step
Epoch 52/100
23/23 - 0s - loss: 0.9955 - mae: 0.7987 - val_loss: 1.0184 - val_mae: 0.7941 - 40ms/epoch - 2ms/step
Epoch 53/100
23/23 - 0s - loss: 0.9947 - mae: 0.7988 - val_loss: 1.0141 - val_mae: 0.791

Epoch 17/100
23/23 - 0s - loss: 1.0026 - mae: 0.8005 - val_loss: 1.0242 - val_mae: 0.7907 - 40ms/epoch - 2ms/step
Epoch 18/100
23/23 - 0s - loss: 1.0022 - mae: 0.8004 - val_loss: 1.0241 - val_mae: 0.7906 - 41ms/epoch - 2ms/step
Epoch 19/100
23/23 - 0s - loss: 1.0024 - mae: 0.8004 - val_loss: 1.0247 - val_mae: 0.7921 - 37ms/epoch - 2ms/step
Epoch 20/100
23/23 - 0s - loss: 1.0017 - mae: 0.8001 - val_loss: 1.0277 - val_mae: 0.7939 - 40ms/epoch - 2ms/step
Epoch 21/100
23/23 - 0s - loss: 1.0015 - mae: 0.8001 - val_loss: 1.0209 - val_mae: 0.7894 - 39ms/epoch - 2ms/step
Epoch 22/100
23/23 - 0s - loss: 1.0014 - mae: 0.8005 - val_loss: 1.0212 - val_mae: 0.7900 - 39ms/epoch - 2ms/step
Epoch 23/100
23/23 - 0s - loss: 1.0012 - mae: 0.8002 - val_loss: 1.0227 - val_mae: 0.7912 - 40ms/epoch - 2ms/step
Epoch 24/100
23/23 - 0s - loss: 0.9994 - mae: 0.7993 - val_loss: 1.0203 - val_mae: 0.7901 - 39ms/epoch - 2ms/step
Epoch 25/100
23/23 - 0s - loss: 0.9995 - mae: 0.7996 - val_loss: 1.0212 - val_mae: 0.790

Epoch 89/100
23/23 - 0s - loss: 0.9915 - mae: 0.7977 - val_loss: 1.0186 - val_mae: 0.7947 - 41ms/epoch - 2ms/step
Epoch 90/100
23/23 - 0s - loss: 0.9924 - mae: 0.7985 - val_loss: 1.0195 - val_mae: 0.7964 - 41ms/epoch - 2ms/step
Epoch 91/100
23/23 - 0s - loss: 0.9911 - mae: 0.7975 - val_loss: 1.0194 - val_mae: 0.7960 - 37ms/epoch - 2ms/step
Epoch 92/100
23/23 - 0s - loss: 0.9906 - mae: 0.7974 - val_loss: 1.0180 - val_mae: 0.7951 - 40ms/epoch - 2ms/step
Epoch 93/100
23/23 - 0s - loss: 0.9911 - mae: 0.7975 - val_loss: 1.0198 - val_mae: 0.7963 - 38ms/epoch - 2ms/step
Epoch 94/100
23/23 - 0s - loss: 0.9905 - mae: 0.7972 - val_loss: 1.0173 - val_mae: 0.7949 - 41ms/epoch - 2ms/step
Epoch 95/100
23/23 - 0s - loss: 0.9926 - mae: 0.7984 - val_loss: 1.0211 - val_mae: 0.7979 - 39ms/epoch - 2ms/step
Epoch 96/100
23/23 - 0s - loss: 0.9916 - mae: 0.7978 - val_loss: 1.0222 - val_mae: 0.7982 - 39ms/epoch - 2ms/step
Epoch 97/100
23/23 - 0s - loss: 0.9931 - mae: 0.7977 - val_loss: 1.0171 - val_mae: 0.794

...

Epoch 57/100
23/23 - 0s - loss: 0.9967 - mae: 0.7997 - val_loss: 1.0411 - val_mae: 0.8085 - 48ms/epoch - 2ms/step
Epoch 58/100
23/23 - 0s - loss: 1.0062 - mae: 0.8052 - val_loss: 1.0116 - val_mae: 0.7895 - 42ms/epoch - 2ms/step
Epoch 59/100
23/23 - 0s - loss: 1.0015 - mae: 0.8012 - val_loss: 1.0169 - val_mae: 0.7951 - 44ms/epoch - 2ms/step
Epoch 60/100
23/23 - 0s - loss: 0.9978 - mae: 0.8006 - val_loss: 1.0126 - val_mae: 0.7866 - 44ms/epoch - 2ms/step
Epoch 61/100
23/23 - 0s - loss: 1.0050 - mae: 0.8035 - val_loss: 1.0114 - val_mae: 0.7901 - 40ms/epoch - 2ms/step
Epoch 62/100
23/23 - 0s - loss: 0.9957 - mae: 0.8008 - val_loss: 1.0522 - val_mae: 0.8080 - 41ms/epoch - 2ms/step
Epoch 63/100
23/23 - 0s - loss: 0.9995 - mae: 0.7993 - val_loss: 1.0421 - val_mae: 0.8085 - 41ms/epoch - 2ms/step
Epoch 64/100
23/23 - 0s - loss: 1.0028 - mae: 0.8016 - val_loss: 1.0218 - val_mae: 0.7986 - 39ms/epoch - 2ms/step
Epoch 65/100
23/23 - 0s - loss: 1.0011 - mae: 0.8025 - val_loss: 1.0149 - val_mae: 0.794

Epoch 29/100
23/23 - 0s - loss: 1.0073 - mae: 0.8037 - val_loss: 1.0251 - val_mae: 0.8004 - 40ms/epoch - 2ms/step
Epoch 30/100
23/23 - 0s - loss: 1.0123 - mae: 0.8066 - val_loss: 1.0402 - val_mae: 0.8082 - 38ms/epoch - 2ms/step
Epoch 31/100
23/23 - 0s - loss: 1.0051 - mae: 0.8018 - val_loss: 1.0272 - val_mae: 0.8015 - 46ms/epoch - 2ms/step
Epoch 32/100
23/23 - 0s - loss: 1.0163 - mae: 0.8057 - val_loss: 1.0694 - val_mae: 0.8208 - 39ms/epoch - 2ms/step
Epoch 33/100
23/23 - 0s - loss: 1.0092 - mae: 0.8034 - val_loss: 1.0464 - val_mae: 0.8119 - 39ms/epoch - 2ms/step
Epoch 34/100
23/23 - 0s - loss: 0.9996 - mae: 0.8013 - val_loss: 1.0151 - val_mae: 0.7884 - 40ms/epoch - 2ms/step
Epoch 35/100
23/23 - 0s - loss: 0.9974 - mae: 0.7994 - val_loss: 1.0231 - val_mae: 0.7964 - 40ms/epoch - 2ms/step
Epoch 36/100
23/23 - 0s - loss: 1.0023 - mae: 0.8006 - val_loss: 1.0127 - val_mae: 0.7883 - 40ms/epoch - 2ms/step
Epoch 37/100
23/23 - 0s - loss: 1.0221 - mae: 0.8115 - val_loss: 1.0563 - val_mae: 0.817

7/7 [==============================] - 0s 831us/step
Количество элементов  99    95
Epoch 1/100
23/23 - 1s - loss: 1.0487 - mae: 0.8181 - val_loss: 1.0253 - val_mae: 0.7892 - 707ms/epoch - 31ms/step
Epoch 2/100
23/23 - 0s - loss: 1.0135 - mae: 0.8040 - val_loss: 1.0290 - val_mae: 0.7954 - 41ms/epoch - 2ms/step
Epoch 3/100
23/23 - 0s - loss: 1.0159 - mae: 0.8040 - val_loss: 1.0564 - val_mae: 0.8099 - 41ms/epoch - 2ms/step
Epoch 4/100
23/23 - 0s - loss: 1.0117 - mae: 0.8028 - val_loss: 1.0409 - val_mae: 0.8044 - 40ms/epoch - 2ms/step
Epoch 5/100
23/23 - 0s - loss: 1.0183 - mae: 0.8067 - val_loss: 1.0439 - val_mae: 0.7953 - 40ms/epoch - 2ms/step
Epoch 6/100
23/23 - 0s - loss: 1.0199 - mae: 0.8070 - val_loss: 1.0255 - val_mae: 0.7884 - 40ms/epoch - 2ms/step
Epoch 7/100
23/23 - 0s - loss: 1.0043 - mae: 0.8000 - val_loss: 1.0245 - val_mae: 0.7935 - 39ms/epoch - 2ms/step
Epoch 8/100
23/23 - 0s - loss: 1.0053 - mae: 0.8020 - val_loss: 1.0145 - val_mae: 0.7878 - 39ms/epoch - 2ms/step
Epoch 9/10

Epoch 73/100
23/23 - 0s - loss: 0.9995 - mae: 0.8022 - val_loss: 1.0163 - val_mae: 0.7915 - 41ms/epoch - 2ms/step
Epoch 74/100
23/23 - 0s - loss: 1.0051 - mae: 0.8036 - val_loss: 1.0166 - val_mae: 0.7945 - 40ms/epoch - 2ms/step
Epoch 75/100
23/23 - 0s - loss: 0.9985 - mae: 0.7999 - val_loss: 1.0124 - val_mae: 0.7889 - 39ms/epoch - 2ms/step
Epoch 76/100
23/23 - 0s - loss: 1.0219 - mae: 0.8102 - val_loss: 1.0121 - val_mae: 0.7869 - 41ms/epoch - 2ms/step
Epoch 77/100
23/23 - 0s - loss: 0.9997 - mae: 0.8032 - val_loss: 1.0222 - val_mae: 0.7931 - 41ms/epoch - 2ms/step
Epoch 78/100
23/23 - 0s - loss: 0.9970 - mae: 0.8002 - val_loss: 1.0167 - val_mae: 0.7926 - 39ms/epoch - 2ms/step
Epoch 79/100
23/23 - 0s - loss: 0.9994 - mae: 0.8003 - val_loss: 1.0421 - val_mae: 0.8041 - 41ms/epoch - 2ms/step
Epoch 80/100
23/23 - 0s - loss: 0.9967 - mae: 0.7994 - val_loss: 1.0123 - val_mae: 0.7857 - 40ms/epoch - 2ms/step
Epoch 81/100
23/23 - 0s - loss: 1.0048 - mae: 0.8012 - val_loss: 1.0363 - val_mae: 0.805

Epoch 45/100
23/23 - 0s - loss: 1.0031 - mae: 0.8014 - val_loss: 1.0486 - val_mae: 0.8069 - 39ms/epoch - 2ms/step
Epoch 46/100
23/23 - 0s - loss: 1.0056 - mae: 0.8045 - val_loss: 1.0559 - val_mae: 0.8109 - 40ms/epoch - 2ms/step
Epoch 47/100
23/23 - 0s - loss: 1.0107 - mae: 0.8054 - val_loss: 1.0532 - val_mae: 0.8147 - 40ms/epoch - 2ms/step
Epoch 48/100
23/23 - 0s - loss: 1.0032 - mae: 0.8000 - val_loss: 1.0408 - val_mae: 0.8000 - 39ms/epoch - 2ms/step
Epoch 49/100
23/23 - 0s - loss: 1.0079 - mae: 0.8029 - val_loss: 1.0469 - val_mae: 0.8078 - 39ms/epoch - 2ms/step
Epoch 50/100
23/23 - 0s - loss: 1.0131 - mae: 0.8061 - val_loss: 1.0114 - val_mae: 0.7879 - 39ms/epoch - 2ms/step
Epoch 51/100
23/23 - 0s - loss: 1.0099 - mae: 0.8052 - val_loss: 1.0155 - val_mae: 0.7917 - 40ms/epoch - 2ms/step
Epoch 52/100
23/23 - 0s - loss: 1.0177 - mae: 0.8091 - val_loss: 1.0137 - val_mae: 0.7876 - 40ms/epoch - 2ms/step
Epoch 53/100
23/23 - 0s - loss: 1.0002 - mae: 0.8031 - val_loss: 1.0119 - val_mae: 0.789

In [32]:
modelsMAE

[[11, 2.460988142772665, 361.40824067405435],
 [12, 2.4561492101705547, 359.34371236228384],
 [13, 2.4571583728007713, 359.935470977101],
 [14, 2.455155636019799, 360.94629115868736],
 [15, 2.456451445843668, 358.98197627203166],
 [16, 2.460861102084523, 358.7470632495533],
 [17, 2.4561569631830915, 358.7746824554091],
 [18, 2.460649871812888, 359.98497208955547],
 [19, 2.4620555276554867, 358.97323912359906],
 [20, 2.4525028827527766, 360.73508046417436],
 [21, 2.4589237030456266, 360.3963810432748],
 [22, 2.451957633187048, 361.1998277488542],
 [23, 2.455049361420645, 360.25972199428105],
 [24, 2.4468106277643447, 358.4280839476824],
 [25, 2.444551837881104, 359.49409032027273],
 [26, 2.456978281873275, 360.8446673548702],
 [27, 2.4543132464840784, 360.47134392790696],
 [28, 2.4441343441009256, 359.0622612677764],
 [29, 2.4574407364067397, 359.3898146399934],
 [30, 2.4619623769655368, 358.8868846281171],
 [31, 2.448570711993911, 359.42367135594264],
 [32, 2.4536407427355234, 359.1443

###### Выводы к разделу 3.4
1. Наилучшие результаты предсказания свойств композитных матералов показала полносвязная нейронная сеть имеющая следующую архитектуру:
    - входной слой (11 входов)
    - 1 скрытый слой (16 нейронов)
    - 2 скрытый слой (32 нейрона)
    - выходной слой (2 нейрона)
2. Наилучшие результаты модель показала на стандартизованных данных при кодировании признака "Угол нашивки, град".